In [1]:
# Основные библиотеки
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from pathlib import Path
import warnings
warnings.filterwarnings('ignore')

# Обработка текста
import re
from collections import Counter, defaultdict
import string

# NLP библиотеки
try:
    import spacy
    nlp = spacy.load('ru_core_news_sm')
    SPACY_AVAILABLE = True
except:
    SPACY_AVAILABLE = False
    print("⚠️ Русская модель SpaCy недоступна. Некоторые NLP функции будут ограничены.")

# Библиотеки для сходства и машинного обучения
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans, DBSCAN
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

# Нечеткое сопоставление
from rapidfuzz import fuzz, process
from fuzzywuzzy import fuzz as fuzz_wuzzy

# Визуализация
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.offline as pyo
pyo.init_notebook_mode(connected=True)

# Импорты проекта SAMe
import sys
sys.path.append('../../src')

try:
    from same_api.data_manager import data_helper
    from same_clear.text_processing.text_cleaner import TextCleaner, CleaningConfig
    from same_clear.text_processing.lemmatizer import Lemmatizer, LemmatizerConfig
    from same_clear.text_processing.normalizer import TextNormalizer, NormalizerConfig
    SAME_MODULES_AVAILABLE = True
    print("✅ Модули SAMe успешно загружены")
except ImportError as e:
    SAME_MODULES_AVAILABLE = False
    print(f"⚠️ Модули SAMe недоступны: {e}")

# Конфигурация
plt.style.use('seaborn-v0_8')
sns.set_palette("husl")
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)

print("🚀 Настройка завершена успешно!")

✅ Модули SAMe успешно загружены
🚀 Настройка завершена успешно!


In [2]:
# df = pd.read_csv(data_helper["data"] / "output/full_3_advanced.csv")
df = pd.read_csv("catalog_with_clusters.csv")
df_dubl = pd.read_csv(data_helper["data"] / "output/catalog_with_dbscan_clusters.csv")
df["Cluster_ID_DBSCAN"] = df_dubl["Cluster_ID_DBSCAN"]
print(len(df))

130303


In [3]:
# === Очистка и нормализация текста ===
def normalize(text):
    text = str(text).lower()
    delete = [")", "(", ":", ";", "!", "?", "№", "#", "%", "/",
              ".", ",", "-"]
    
    for d in delete:
        text = text.replace(d, "")
    
    text = re.sub(r'<[^>]*>', '', text)

    text = text.strip()
    text = re.sub(r'\s+', ' ', text)

    text = text.replace("color", "").replace("num", "")

    text = re.sub(r'[^\w\s]', ' ', text)
    text = re.sub(r'\s+', ' ', text).strip()
    text = " ".join(filter(lambda x: not any([c.isdigit() for c in x]), text.split()))
    return text

In [ ]:
def adaptive_threshold(name1, name2):
    avg_len = (len(name1) + len(name2)) / 2
    if avg_len < 30:
        return 85 
    elif avg_len < 60:
        return 70
    else:
        return 50

In [5]:

from tqdm import tqdm
from datasketch import MinHash, MinHashLSH

# === Параметры ===
THRESHOLD = 20  # Порог схожести RapidFuzz (0–100)
SHINGLE_SIZE = 5  # Размер шинглов для MinHash
NUM_PERM = 128  # Количество перестановок для MinHash

# === Загрузка данных ===
# df = pd.read_csv(INPUT_CSV)
df['Normalized'] = df['Lemmatized_Name'].apply(normalize)


In [6]:
# === Генерация шинглов для MinHash ===
def get_minhash(text):
    m = MinHash(num_perm=NUM_PERM)
    shingles = set([text[i:i+SHINGLE_SIZE] for i in range(len(text)-SHINGLE_SIZE + 1)])
    for s in shingles:
        m.update(s.encode('utf8'))
    return m

In [7]:

# === Построение LSH для быстрого поиска ===
print("🔍 Строим MinHash LSH индекс...")
lsh = MinHashLSH(threshold=THRESHOLD/100, num_perm=NUM_PERM)
minhashes = {}

for idx, row in tqdm(df.iterrows(), total=len(df)):
    m = get_minhash(row['Normalized'])
    lsh.insert(str(idx), m)
    minhashes[str(idx)] = m
    
# === Поиск кластеров аналогов ===
print("🔄 Поиск схожих товаров...")
clusters = []
visited = set()

for idx in tqdm(df.index):
    idx_str = str(idx)
    if idx_str in visited:
        continue

    m = minhashes[idx_str]
    similar = lsh.query(m)

    # RapidFuzz для точной фильтрации
    group = []
    for sim_idx in similar:
        if sim_idx == idx_str or sim_idx in visited:
            continue
        
        name1 = df.loc[int(idx_str), 'Normalized']
        name2 = df.loc[int(sim_idx), 'Normalized']
        score = fuzz_wuzzy.token_set_ratio(name1, name2)
        threshold = adaptive_threshold(name1, name2)
        
        if score >= threshold:
            group.append(int(sim_idx))

    if group:
        group.append(idx)  
        clusters.append(sorted(set(group)))
        visited.update(map(str, group))

print(f"\n📦 Найдено кластеров аналогов: {len(clusters)}")
cluster_map = {}
for cluster_id, group in enumerate(clusters):
    for i in group:
        cluster_map[i] = cluster_id

df['Cluster_ID'] = df.index.map(lambda x: cluster_map.get(x, -1))
df.to_csv("catalog_with_clusters.csv", index=False)
print("✅ Результат сохранён в catalog_with_clusters.csv")

🔍 Строим MinHash LSH индекс...


100%|██████████| 130303/130303 [01:03<00:00, 2046.10it/s]


🔄 Поиск схожих товаров...


100%|██████████| 130303/130303 [00:56<00:00, 2323.42it/s] 



📦 Найдено кластеров аналогов: 12879
✅ Результат сохранён в catalog_with_clusters.csv


In [ ]:
vectorizer = TfidfVectorizer(ngram_range=(1, 3), min_df=2)
X = vectorizer.fit_transform(df['Normalized'])  # df['Normalized'] — твои очищенные тексты

In [ ]:
# Суммируем TF-IDF значения по всем документам (ось 0)
tfidf_sums = np.asarray(X.sum(axis=0)).ravel()

# Сопоставим n-граммы и их суммарный TF-IDF
terms = vectorizer.get_feature_names_out()
tfidf_df = pd.DataFrame({'ngram': terms, 'tfidf': tfidf_sums})

# Сортируем по значимости
tfidf_df = tfidf_df.sort_values(by='tfidf', ascending=False)

In [ ]:
import seaborn as sns

plt.figure(figsize=(12, 8))
top_n = 30
sns.barplot(data=tfidf_df.head(top_n), x='tfidf', y='ngram', palette='viridis')
plt.title(f'🔝 Top {top_n} n-грамм по суммарному TF-IDF')
plt.xlabel('Суммарное TF-IDF значение')
plt.ylabel('N-грамма')
plt.tight_layout()
plt.show()

In [ ]:
# === TF-IDF преобразование ===
print("🔠 Преобразуем текст в TF-IDF векторы...")
vectorizer = TfidfVectorizer(ngram_range=(1, 3), min_df=2)
X = vectorizer.fit_transform(df['Normalized'])

# === Кластеризация DBSCAN ===
print("🔄 Запускаем DBSCAN кластеризацию...")
db = DBSCAN(eps=0.35, min_samples=2, metric='cosine', n_jobs=-1)
labels = db.fit_predict(X)

# # === Присваиваем кластеры ===
df['Cluster_ID_DBSCAN'] = labels

# === Сохраняем результат ===
df.to_csv("catalog_with_dbscan_clusters.csv", index=False)
print(f"📦 Сохранено в catalog_with_dbscan_clusters.csv. Найдено кластеров: {len(set(labels)) - (1 if -1 in labels else 0)}")
print(f"❗ Элементов без кластера (label == -1): {(labels == -1).sum()}")

In [35]:

# === Генерация шинглов для MinHash ===
def get_minhash(text):
    m = MinHash(num_perm=NUM_PERM)
    shingles = set([text[i:i+SHINGLE_SIZE] for i in range(len(text)-SHINGLE_SIZE + 1)])
    for s in shingles:
        m.update(s.encode('utf8'))
    return m

In [37]:

# === Построение LSH для быстрого поиска ===
print("🔍 Строим MinHash LSH индекс...")
lsh = MinHashLSH(threshold=THRESHOLD/100, num_perm=NUM_PERM)
minhashes = {}

for idx, row in tqdm(df.iterrows(), total=len(df)):
    m = get_minhash(row['Normalized'])
    lsh.insert(str(idx), m)
    minhashes[str(idx)] = m
    
# === Поиск кластеров аналогов ===
print("🔄 Поиск схожих товаров...")
clusters = []
visited = set()

for idx in tqdm(df.index):
    idx_str = str(idx)
    if idx_str in visited:
        continue

    m = minhashes[idx_str]
    similar = lsh.query(m)

    # RapidFuzz для точной фильтрации
    group = []
    for sim_idx in similar:
        if sim_idx == idx_str or sim_idx in visited:
            continue

        score = fuzz_wuzzy.token_set_ratio(df.loc[int(idx_str), 'Normalized'], df.loc[int(sim_idx), 'Normalized'])
        threshold = adaptive_threshold(df.loc[int(idx_str), 'Normalized'], df.loc[int(sim_idx), 'Normalized'])
        
        if score >= threshold:
            group.append(int(sim_idx))

    if group:
        group.append(idx)  
        clusters.append(sorted(set(group)))
        visited.update(map(str, group))

print(f"\n📦 Найдено кластеров аналогов: {len(clusters)}")
cluster_map = {}
for cluster_id, group in enumerate(clusters):
    for i in group:
        cluster_map[i] = cluster_id

df['Cluster_ID'] = df.index.map(lambda x: cluster_map.get(x, -1))
df.to_csv("catalog_with_clusters.csv", index=False)
print("✅ Результат сохранён в catalog_with_clusters.csv")

🔍 Строим MinHash LSH индекс...


100%|██████████| 130303/130303 [03:08<00:00, 691.72it/s]


🔄 Поиск схожих товаров...


100%|██████████| 130303/130303 [00:49<00:00, 2636.32it/s] 



📦 Найдено кластеров аналогов: 12594
✅ Результат сохранён в catalog_with_clusters.csv


In [ ]:
minhashes

{'0': <datasketch.minhash.MinHash at 0x34a035160>,
 '1': <datasketch.minhash.MinHash at 0x34572f350>,
 '2': <datasketch.minhash.MinHash at 0x34a035430>,
 '3': <datasketch.minhash.MinHash at 0x34a035250>,
 '4': <datasketch.minhash.MinHash at 0x34a035700>,
 '5': <datasketch.minhash.MinHash at 0x34a0356a0>,
 '6': <datasketch.minhash.MinHash at 0x34a035760>,
 '7': <datasketch.minhash.MinHash at 0x34a035670>,
 '8': <datasketch.minhash.MinHash at 0x34a035340>,
 '9': <datasketch.minhash.MinHash at 0x34a035310>,
 '10': <datasketch.minhash.MinHash at 0x34a035280>,
 '11': <datasketch.minhash.MinHash at 0x34a0358e0>,
 '12': <datasketch.minhash.MinHash at 0x34a0354f0>,
 '13': <datasketch.minhash.MinHash at 0x34a0357c0>,
 '14': <datasketch.minhash.MinHash at 0x34a0357f0>,
 '15': <datasketch.minhash.MinHash at 0x34a0358b0>,
 '16': <datasketch.minhash.MinHash at 0x34a035910>,
 '17': <datasketch.minhash.MinHash at 0x34a035c10>,
 '18': <datasketch.minhash.MinHash at 0x34a035b80>,
 '19': <datasketch.min

In [ ]:
# === TF-IDF преобразование ===
print("🔠 Преобразуем текст в TF-IDF векторы...")
vectorizer = TfidfVectorizer(ngram_range=(1, 3), min_df=2)
X = vectorizer.fit_transform(df['Normalized'])

# === Кластеризация DBSCAN ===
print("🔄 Запускаем DBSCAN кластеризацию...")
db = DBSCAN(eps=0.5, min_samples=3, metric='cosine', n_jobs=-1)
labels = db.fit_predict(X)

# # === Присваиваем кластеры ===
df['Cluster_ID_DBSCAN'] = labels

# === Сохраняем результат ===
df.to_csv("catalog_with_dbscan_clusters.csv", index=False)
print(f"📦 Сохранено в catalog_with_dbscan_clusters.csv. Найдено кластеров: {len(set(labels)) - (1 if -1 in labels else 0)}")
print(f"❗ Элементов без кластера (label == -1): {(labels == -1).sum()}")

🔠 Преобразуем текст в TF-IDF векторы...
🔄 Запускаем DBSCAN кластеризацию...


In [38]:
!pip install sentence-transformers lightgbm xgboost scikit-learn pandas

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 10.2 MB/s eta 0:00:0031m? eta -:--:--
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 21.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2/2 [lightgbm]


In [43]:
len(df[df['Cluster_ID_DBSCAN'] != -1])

104566

In [59]:
world_avg = 0
count = 0
max_worlds = 0
min_worlds = 1000
count_none = 0
count_n = 0
for i, row in df.iterrows():
    text = row["Normalized"].split()
    if len(text) == 0:
        count_none += 1
    elif len(text) >= 10:
        # print(row["Normalized"])
        count_n += 1
    world_avg += len(text)
    count += 1
    max_worlds = max(max_worlds, len(text))
    min_worlds = min(min_worlds, len(text))
world_avg /= count

print(f"world_avg: {world_avg}, max_worlds: {max_worlds}, min_worlds: {min_worlds}")
print(f"{count_none=} {count_n=}")

world_avg: 4.377688925043936, max_worlds: 20, min_worlds: 0
count_none=38 count_n=5422


In [90]:
def get_buffer_row_world(df_group):
    buffer_row_world = []
    for text in df_group["Normalized"]:
        if len(text.split()) == 0:
            continue
        text_first = text.split()[0]
        if text_first in buffer_row_world:
            continue
        buffer_row_world.append(text_first)

    return buffer_row_world

In [ ]:
unclustered = df[df["Cluster_ID_DBSCAN"] == -1]
clustered = df[df["Cluster_ID_DBSCAN"] != -1]


In [93]:
len(df["Cluster_ID_DBSCAN"].unique())

6147

In [120]:
import networkx as nx

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from collections import defaultdict


unclustered = df[df["Cluster_ID_DBSCAN"] == -1]
clustered = df[df["Cluster_ID_DBSCAN"] != -1]
group_clustered = clustered.groupby("Cluster_ID_DBSCAN")
buffer = []
buffer_row_world = {}
concat_id = []
for i, df_group in group_clustered:
    worlds = get_buffer_row_world(df_group)

    buffer_row_world[i] = worlds

# Создаем "документы" из слов
cluster_ids = list(buffer_row_world.keys())
texts = [" ".join(words) for words in buffer_row_world.values()]

In [ ]:
# TF-IDF
vectorizer = TfidfVectorizer()
tfidf_matrix = vectorizer.fit_transform(texts)

# Сходство
similarity = cosine_similarity(tfidf_matrix)

# Порог — выше этого считаем кластеры похожими
THRESHOLD = 0.7

In [ ]:

# Группировка через слияние кластеров
merged = {}
visited = set()
new_cluster_id = 0
for i in range(len(cluster_ids)):
    if cluster_ids[i] in visited:
        continue
    group = [cluster_ids[i]]
    visited.add(cluster_ids[i])
    for j in range(i + 1, len(cluster_ids)):
        if similarity[i, j] >= THRESHOLD:
            group.append(cluster_ids[j])
            visited.add(cluster_ids[j])
    merged[new_cluster_id] = group
    new_cluster_id += 1

for group_id, cluster_group in merged.items():
    if len(cluster_group) <= 1:
        continue

    # Используем первый кластер как основной
    main_cluster_id = cluster_group[0]

    # Обновляем текущий кластер и все связанные с ним на основной
    df.loc[df["Cluster_ID_DBSCAN"] == group_id, "Cluster_ID_DBSCAN"] = main_cluster_id
    for cluster_group_id in cluster_group[1:]:
        df.loc[df["Cluster_ID_DBSCAN"] == cluster_group_id, "Cluster_ID_DBSCAN"] = main_cluster_id

In [121]:
# Строим граф связей между кластерами
G = nx.Graph()

# Добавляем связи из словаря merged
for main_cluster, group in merged.items():
    for other_cluster in group:
        G.add_edge(main_cluster, other_cluster)

# Находим компоненты связности
connected_components = list(nx.connected_components(G))

# Создаём отображение: старый_cluster_id → новый_cluster_id (представитель компоненты)
cluster_mapping = {}
for component in connected_components:
    representative = min(component)  # или любой другой критерий
    for cluster_id in component:
        cluster_mapping[cluster_id] = representative

# Обновляем кластерные метки в датафрейме
df["Cluster_ID_DBSCAN"] = df["Cluster_ID_DBSCAN"].apply(
    lambda cid: cluster_mapping.get(cid, cid))

In [94]:
unclustered = df[df["Cluster_ID_DBSCAN"] == -1]
clustered = df[df["Cluster_ID_DBSCAN"] != -1]
group_clustered = clustered.groupby("Cluster_ID_DBSCAN")
buffer = []
buffer_row_world = {}
concat_id = []
for i, df_group in group_clustered:
    worlds = get_buffer_row_world(df_group)
    # if len(worlds) > 100:
    #     buffer_row_world[i] = worlds
    #     continue

    buffer_row_world[i] = worlds

    # for word in worlds:
        

# print(len(buffer_row_world))
# for i, row in buffer_row_world.items():
#     if str(i).isdigit():
#         continue
#     print(f"{i}: {row}")

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from collections import defaultdict

unclustered = df[df["Cluster_ID_DBSCAN"] == -1]
clustered = df[df["Cluster_ID_DBSCAN"] != -1]
group_clustered = clustered.groupby("Cluster_ID_DBSCAN")
buffer = []
buffer_row_world = {}
concat_id = []
for i, df_group in group_clustered:
    worlds = get_buffer_row_world(df_group)

    buffer_row_world[i] = worlds

# Создаем "документы" из слов
cluster_ids = list(buffer_row_world.keys())
texts = [" ".join(words) for words in buffer_row_world.values()]

In [ ]:
# TF-IDF
vectorizer = TfidfVectorizer()
tfidf_matrix = vectorizer.fit_transform(texts)

# Сходство
similarity = cosine_similarity(tfidf_matrix)

# Порог — выше этого считаем кластеры похожими
THRESHOLD = 0.7

In [108]:
# Группировка через слияние кластеров
merged = {}
visited = set()
new_cluster_id = 0
for i in range(len(cluster_ids)):
    if cluster_ids[i] in visited:
        continue
    group = [cluster_ids[i]]
    visited.add(cluster_ids[i])
    for j in range(i + 1, len(cluster_ids)):
        if similarity[i, j] >= THRESHOLD:
            group.append(cluster_ids[j])
            visited.add(cluster_ids[j])
    merged[new_cluster_id] = group
    new_cluster_id += 1

for group_id, cluster_group in merged.items():
    if len(cluster_group) <= 1:
        continue

    # Используем первый кластер как основной
    main_cluster_id = cluster_group[0]

    # Обновляем текущий кластер и все связанные с ним на основной
    df.loc[df["Cluster_ID_DBSCAN"] == group_id, "Cluster_ID_DBSCAN"] = main_cluster_id
    for cluster_group_id in cluster_group[1:]:
        df.loc[df["Cluster_ID_DBSCAN"] == cluster_group_id, "Cluster_ID_DBSCAN"] = main_cluster_id

# for group_id, cluster_group in merged.items():
#     if len(cluster_group) <= 1:
#         continue
#     print(df[df["Cluster_ID_DBSCAN"] == group_id]["Raw_Name"])
#     print(cluster_group)
#     [print(df[df["Cluster_ID_DBSCAN"] == cluster_group_id]["Raw_Name"]) for cluster_group_id in cluster_group]

#     break

In [109]:
df.groupby("Cluster_ID_DBSCAN").size().reset_index(name="Count").sort_values(by="Count", ascending=False)

Cluster_ID_DBSCAN  Count
2                     1  60321
0                    -1  25737
713                3705   3001
70                  477   1615
59                  311   1374
...                 ...    ...
674                3525      3
671                3513      3
669                3506      3
665                3477      3
1064               6141      3

[1065 rows x 2 columns]

In [122]:
df.groupby("Cluster_ID_DBSCAN").size().reset_index(name="Count").sort_values(by="Count", ascending=False)

Cluster_ID_DBSCAN  Count
2                  1  60321
3                  2  44242
0                 -1  25737
1                  0      3

In [ ]:
#3705
# ['ерш',
#  'костюм', ----------------------
#  'сапог',   2----------------------
#  'фартук',
#  'бокорезы',
#  'длинногубцы',
#  'плоскогубцы',
#  'кабель',   1----------------------
#  'адаптер',
#  'изоляция',
#  'термостат',
#  'рубашка',  3----------------------
#  'услуга'] 4----------------------

#477
# ['бандаж',
#  'батарейка',
#  'бельё',
#  'ботинок',
#  'вешалка',
#  'диск',
#  'зеркало',
#  'комплект',    6----------------------
#  'наковальня',
#  'полуботинок',
#  'пульт',
#  'реле',
#  'сапог',         2----------------------
#  'тумба',
#  'электрическийпит',
#  'питание',
#  'кабель',        1----------------------
#  'штанга',
#  'ботинки',
#  'костюм',        ----------------------
#  'батарея']

#311
# ['бафф',
#  'бланк',
#  'брюки',
#  'вставка',
#  'замок',
#  'защёлка',
#  'куртка',
#  'перчатка',
#  'полукомбинезон',
#  'свитер',
#  'термобелье',
#  'вкладыш',
#  'памятка',
#  'пускатель',
#  'секрет',
#  'контакт',
#  'разъём',
#  'предохранитель',
#  'контактор',  5----------------------
#  'обрамление',
#  'поло',
#  'шпатель',
#  'гильза',
#  'гидротестер',
#  'уплотнение',
#  'костюм',     ----------------------
#  'комбинезон',
#  'рубашка',   3----------------------
#  'толстовка',
#  'кепка',
#  'стол',
#  'гайка',
#  'наконечник',
#  'штифт']

# 1832
# ['двигатель', 
# 'комплект',   6----------------------
# 'контактор',  5----------------------
# 'миксер', 
# 'очиститель', 
# 'услуга']  4----------------------

In [117]:
tokens = []
for i, row in df.iterrows():
    if row["Cluster_ID_DBSCAN"] == 1832:
        text = row["Normalized"].split()[:1]
        for token in text:
            if token in tokens:
                continue
            tokens.append(token)
tokens

['двигатель', 'комплект', 'контактор', 'миксер', 'очиститель', 'услуга']

In [ ]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer("cointegrated/LaBSE-en-ru")  # или любой rus модель
embeddings = model.encode([" ".join(w) for w in clusters.values()], normalize_embeddings=True)
similarity = cosine_similarity(embeddings)

In [ ]:
group_clustered = clustered.groupby("Cluster_ID_DBSCAN")
avg_class_world = group_clustered.size().reset_index(name="Count").sort_values(by="Count", ascending=False)
print(avg_class_world[avg_class_world["Cluster_ID_DBSCAN"] != 1]["Count"].mean())
print(avg_class_world["Count"].mean())

7.200162733930024
17.01366742596811


In [111]:
group_clustered = clustered.groupby("Cluster_ID_DBSCAN")
avg_class_world = group_clustered.size().reset_index(name="Count").sort_values(by="Count", ascending=False)
print(avg_class_world[avg_class_world["Cluster_ID_DBSCAN"] != 1]["Count"].mean())
print(avg_class_world["Count"].mean())

7.200162733930024
17.01366742596811


In [81]:
avg_class_world["Count"]

1       60321
531       587
530       499
4730      476
5821      473
        ...  
3126        3
3131        3
3132        3
3136        3
3073        3
Name: Count, Length: 6146, dtype: int64

In [77]:
for i, row in df.iterrows():
    if row["Cluster_ID_DBSCAN"] == 2:
        print(row["Normalized"])

автошампунь grass active foam truck cуперпена безконтактной мойка грузовик кг
автошампунь grass active foam effect литр
автошампунь grass active foam light миллилитр


In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sentence_transformers import SentenceTransformer
import xgboost as xgb
import lightgbm as lgb
from sklearn.preprocessing import LabelEncoder
# === 1. Загрузка данных ===
# Предположим, у тебя есть DataFrame с колонками: 'text' и 'label'

le = LabelEncoder()
df['label'] = le.fit_transform(df['BPE_Tokens'])

# === 2. Получение эмбеддингов через BERT ===
model = SentenceTransformer('paraphrase-multilingual-MiniLM-L12-v2')  # или другой
embeddings = model.encode(df['Normalized'].tolist(), show_progress_bar=True)

# === 3. Разделение на train/test ===
X_train, X_test, y_train, y_test = train_test_split(embeddings, df['label'], test_size=0.2, random_state=42)

Batches:   0%|          | 0/4072 [00:00<?, ?it/s]

ValueError: Invalid classes inferred from unique values of `y`.  Expected: [    0     1     2 ... 86256 86257 86258], got [     0      1      2 ... 105977 105978 105980]

In [ ]:
# === 4. XGBoost ===
xgb_model = xgb.XGBClassifier(
    objective='multi:softmax',
    num_class=len(set(df['label'])),
    eval_metric='mlogloss',
    use_label_encoder=False
)
xgb_model.fit(X_train, y_train)
y_pred_xgb = xgb_model.predict(X_test)
print("📊 XGBoost:")
print(classification_report(y_test, y_pred_xgb))

In [ ]:
# === 5. LightGBM ===
lgb_model = lgb.LGBMClassifier(
    objective='multiclass',
    num_class=len(set(df['label'])),
    metric='multi_logloss'
)
lgb_model.fit(X_train, y_train)
y_pred_lgb = lgb_model.predict(X_test)
print("📊 LightGBM:")
print(classification_report(y_test, y_pred_lgb))

In [8]:
# import networkx as nx

# G = nx.Graph()
# for group in clusters:
#     for i in group:
#         for j in group:
#             if i != j:
#                 G.add_edge(i, j)

# # Получаем компоненты связности (объединенные кластеры)
# new_clusters = [list(comp) for comp in nx.connected_components(G)]
# cluster_map = {}
# for cluster_id, group in enumerate(new_clusters):
#     for i in group:
#         cluster_map[i] = cluster_id
        
# df['New_Cluster_ID'] = df.index.map(lambda x: cluster_map.get(x, -1))

In [9]:
# unclustered = df[df["Cluster_ID"] == -1]
# clustered = df[df["Cluster_ID"] != -1]

# for idx_un, row_un in unclustered.iterrows():
#     for cluster_id, group in clustered.groupby("Cluster_ID"):
#         count_score = 0
#         best_cluster = -1
#         for idx_cl, row_cl in group.iterrows():
#             score = fuzz.token_set_ratio(row_un['Normalized'], row_cl['Normalized'])
#             if score > best_cluster and score >= 60:  
#                 best_score = score
#                 best_cluster = cluster_id
#                 count_score += 1
#                 if count_score > 1:
#                     break

#         if count_score >= 1:
#             df.at[idx_un, "Cluster_ID_NEW"] = best_cluster
#             break

    # for idx_cl, row_cl in clustered.iterrows():
    #     score = fuzz.token_set_ratio(row_un['Normalized'], row_cl['Normalized'])
    #     if score > best_score and score >= 60:  
    #         best_score = score
    #         best_cluster = row_cl["Cluster_ID"]
    
    # if best_cluster != -1:
    #     df.at[idx_un, "Cluster_ID"] = best_cluster

In [10]:
# def concat_cluster(cluster1, cluster2):
#     max_cluster = max(cluster1, cluster2, key=len)
#     for idx in min(cluster1, cluster2, key=len):
#         if 
#     return cluster1

In [ ]:
# import hdbscan

# clusterer = hdbscan.HDBSCAN(min_cluster_size=3, metric='euclidean')
# clusterer.fit(X)

# Предсказание кластера для новых векторов:
# clusterer.approximate_predict(new_X)

In [ ]:
def start_DBSCAN(db: DBSCAN, vectorizer: TfidfVectorizer, df, eps=0.5, min_samples=3):
    # if min_samples < 1:
        # min_samples = 3
    # print("🔠 Преобразуем текст в TF-IDF векторы...")
    # vectorizer = TfidfVectorizer(ngram_range=(1, 3), min_df=2)
    # X = vectorizer.fit_transform(df['Normalized'])
    # === Кластеризация DBSCAN ===
    # print("🔄 Запускаем DBSCAN кластеризацию...")
    # db = DBSCAN(eps=eps, min_samples=min_samples, metric='cosine', n_jobs=-1)
    labels = db.(X)
    return labels

In [ ]:
epoth = 7
unclustered = df[df["Cluster_ID_DBSCAN"] == -1]
min_samples = 5
eps = 0.5
while epoth:
    print(f"Эпоха {epoth}")
    print(f"Кластеров: {unclustered['Cluster_ID_DBSCAN'].nunique()}")
    print(f"Товаров: {len(unclustered)}")
    labels = start_DBSCAN(db, vectorizer, unclustered, eps, min_samples)

    # === Присваиваем кластеры ===
    unclustered[f'Cluster_ID_DBSCAN_{epoth}'] = labels
    if unclustered[f'Cluster_ID_DBSCAN_{epoth}'].nunique() == 1:
        break
    
    print(f"Кластеров: {unclustered[f'Cluster_ID_DBSCAN_{epoth}'].nunique()}")

    unclustered = unclustered[unclustered[f'Cluster_ID_DBSCAN_{epoth}'] == -1]

    epoth -= 1
    min_samples -= 1
    eps -= 0.05
    if eps < 0.1:
        eps = 0.2
    print("=" * 100)

Эпоха 7
Кластеров: 1
Товаров: 25737
🔠 Преобразуем текст в TF-IDF векторы...
🔄 Запускаем DBSCAN кластеризацию...
Кластеров: 65
Эпоха 6
Кластеров: 1
Товаров: 25167
🔠 Преобразуем текст в TF-IDF векторы...
🔄 Запускаем DBSCAN кластеризацию...
Кластеров: 9
Эпоха 5
Кластеров: 1
Товаров: 25132
🔠 Преобразуем текст в TF-IDF векторы...
🔄 Запускаем DBSCAN кластеризацию...
Кластеров: 56
Эпоха 4
Кластеров: 1
Товаров: 24967
🔠 Преобразуем текст в TF-IDF векторы...
🔄 Запускаем DBSCAN кластеризацию...
Кластеров: 5814
Эпоха 3
Кластеров: 1
Товаров: 13341
🔠 Преобразуем текст в TF-IDF векторы...
🔄 Запускаем DBSCAN кластеризацию...
Кластеров: 13006
Эпоха 2
Кластеров: 1
Товаров: 194
🔠 Преобразуем текст в TF-IDF векторы...


ValueError: After pruning, no terms remain. Try a lower min_df or a higher max_df.

In [105]:
clustered.groupby("Cluster_ID_DBSCAN").size().reset_index(name="Count").sort_values(by="Count", ascending=False)

Cluster_ID_DBSCAN  Count
1                     1  60321
531                 531    587
530                 530    499
4730               4730    476
5821               5821    473
...                 ...    ...
3126               3126      3
3131               3131      3
3132               3132      3
3136               3136      3
3073               3073      3

[6146 rows x 2 columns]

In [ ]:
for i, row in clustered.iterrows():
    if row["Cluster_ID_DBSCAN"] == -1:
        print(row["Код"], row["Normalized"])

НИ-IS0032430 cветильник led панель 50w 6500k ip40 1200 миллиметр дпо призма neox
НИ-IS0040225 cветильник потолочный osairous 30вт led 6500 светодиодный потолочный
НИ-IS0047648 cпрей ванный комната sanfor санфор 500 миллилитр
НИ-IS0047649 cпрей ультрабелый sanfor санфор 500 миллилитр
НИ-IS0047659 cредство чистить биолан 400 сочный яблоко нэфис
НИ-IS0023737 cтиральный порошок персил 21 килограмм
НИ-IS0047372 cтроп цепной сц одноветвевой стандартный2 метр
НИ-IS0009665 автоаптечка ремонтта покрышка камера арк
НИ-IS0052984 автолампа а24 5 24v маяк россия
НИ-IS0046878 автомат дифференциальный авдт c 4p 32a характеристика
НИ-IS0046879 автомат дифференциальный авдт c 4p 20a характеристика
НИ-IS0031012 автоматический выключатель постоянный ток nb1 63dc 2p c2a dc500b 6ka chint
НИ-IS0034255 автотрансформатор латр tdgc25 аосн andeli
НИ-IS0043025 адаптер фитинг пистолет керхер hd м22 внеш easy lock 22внут
НИ-IS0031299 адаптер bspш bspг
НИ-IS0037104 адаптер миллиметр высота резьба 30 мм hp s1047a
НИ

In [ ]:
df.head(10)

Код                                       Наименование  \
0  НИ-IS0032430  Cветильник LED панель 50W 6500k IP40 1200мм ДП...   
1  НИ-IS0040225  Cветильник потолочный,Osairous,Белый, 30Вт LED...   
2  НИ-IS0014483  Cистема IP-DECT Yealink W80DM контроллер микро...   
3  НИ-IS0047648     Cпрей для ванной комнаты Sanfor (Санфор) 500мл   
4  НИ-IS0047649            Cпрей ультрабелый Sanfor (Санфор) 500мл   
5  НИ-IS0047659  Cредство чистящее Биолан 400г Сочное яблоко (Н...   
6  НИ-IS0023737                   Cтиральный порошок Персил 2.1 кг   
7  НИ-IS0047372  Cтроп цепной 1СЦ (одноветвевой стандартный)-2т 4м   
8  НИ-000043138        Cухой паек Офицерский Армейские Будни РПС-У   
9  НИ-IS0000748     Dallas Lock 8/0-C (СЗИ НСД ,СКН ) (ПО) (до 10)   

                                  НаименованиеПолное           Группа  \
0  Cветильник LED панель 50W 6500k IP40 1200мм ДП...  АВАНСОВЫЙ ОТЧЕТ   
1  Cветильник потолочный,Osairous,Белый, 30Вт LED...  АВАНСОВЫЙ ОТЧЕТ   
2  Cистема IP-DECT Yealink W80DM контроллер микро...  АВАНСОВЫЙ ОТЧЕТ   
3     Cпрей для ванной комнаты Sanfor (Санфор) 500мл  АВАНСОВЫЙ ОТЧЕТ   
4            Cпрей ультрабелый Sanfor (Санфор) 500мл  АВАНСОВЫЙ ОТЧЕТ   
5  Cредство чистящее Биолан 400г Сочное яблоко (Н...  АВАНСОВЫЙ ОТЧЕТ   
6                   Порошок стиральный Персил 2.1 кг  АВАНСОВЫЙ ОТЧЕТ   
7  Cтроп цепной 1СЦ (одноветвевой стандартный)-2т 4м  АВАНСОВЫЙ ОТЧЕТ   
8        Cухой паек Офицерский Армейские Будни РПС-У  АВАНСОВЫЙ ОТЧЕТ   
9     Dallas Lock 8/0-C (СЗИ НСД ,СКН ) (ПО) (до 10)  АВАНСОВЫЙ ОТЧЕТ   

                            ВидНоменклатуры ЕдиницаИзмерения  \
0  Инвентарь и хозяйственные принадлежности               шт   
1                         Сырье и материалы               шт   
2  Инвентарь и хозяйственные принадлежности               шт   
3                         Сырье и материалы               шт   
4                         Сырье и материалы               шт   
5                         Сырье и материалы               шт   
6                         Сырье и материалы               шт   
7  Инвентарь и хозяйственные принадлежности               шт   
8                                    Товары               шт   
9  Инвентарь и хозяйственные принадлежности               шт   

                                            Raw_Name  \
0  Cветильник LED панель 50W 6500k IP40 1200мм ДП...   
1  Cветильник потолочный,Osairous,Белый, 30Вт LED...   
2  Cистема IP-DECT Yealink W80DM контроллер микро...   
3     Cпрей для ванной комнаты Sanfor (Санфор) 500мл   
4            Cпрей ультрабелый Sanfor (Санфор) 500мл   
5  Cредство чистящее Биолан 400г Сочное яблоко (Н...   
6                   Cтиральный порошок Персил 2.1 кг   
7  Cтроп цепной 1СЦ (одноветвевой стандартный)-2т 4м   
8        Cухой паек Офицерский Армейские Будни РПС-У   
9     Dallas Lock 8/0-C (СЗИ НСД ,СКН ) (ПО) (до 10)   

                                        Cleaned_Name  \
0  Cветильник LED панель 50W 6500k IP40 1200мм ДП...   
1  Cветильник потолочный,Osairous,Белый, 30Вт LED...   
2  Cистема IP-DECT Yealink W80DM контроллер микро...   
3     Cпрей для ванной комнаты Sanfor (Санфор) 500мл   
4            Cпрей ультрабелый Sanfor (Санфор) 500мл   
5  Cредство чистящее Биолан 400г Сочное яблоко (Н...   
6                   Cтиральный порошок Персил 2.1 кг   
7  Cтроп цепной 1СЦ (одноветвевой стандартный)-2т 4м   
8        Cухой паек Офицерский Армейские Будни РПС-У   
9     Dallas Lock 8 0-C (СЗИ НСД ,СКН ) (ПО) (до 10)   

                                     Lemmatized_Name  \
0  cветильник led панель 50w 6500k ip40 1200 милл...   
1  cветильник потолочный osairous,<color 30вт led...   
2  cистема ip dect yealink w80dm контроллер микро...   
3   cпрей ванный комната sanfor санфор 500 миллилитр   
4      cпрей ультрабелый sanfor санфор 500 миллилитр   
5    cредство чистить биолан 400 сочный яблоко нэфис   
6            cтиральный порошок персил 2.1 килограмм   
7  cтроп цепной num сц одноветвевой стандартный)-.

In [ ]:
len(df["Cluster_ID"].unique())
#20200
#18816

14937

In [ ]:
len(df["Cluster_ID_DBSCAN"].unique())

6147

In [106]:
df.groupby("Cluster_ID_DBSCAN").size().reset_index(name="Count").sort_values(by="Count", ascending=False)

Cluster_ID_DBSCAN  Count
2                     1  60321
0                    -1  25737
532                 531    587
531                 530    499
4731               4730    476
...                 ...    ...
2390               2389      3
4298               4297      3
4299               4298      3
2389               2388      3
4694               4693      3

[6147 rows x 2 columns]

In [ ]:
df.groupby("Cluster_ID").size().reset_index(name="Count").sort_values(by="Count", ascending=False)

Cluster_ID  Count
0             -1  16226
1593        1592   1064
1796        1795    809
800          799    624
93            92    600
...          ...    ...
1411        1410      2
8947        8946      2
8946        8945      2
8945        8944      2
9179        9178      2

[14937 rows x 2 columns]

In [ ]:
df.groupby("New_Cluster_ID").size().reset_index(name="Count").sort_values(by="Count", ascending=False)

New_Cluster_ID  Count
0                  -1  43289
2097             2096    794
976               975    771
961               960    610
1928             1927    511
...               ...    ...
11825           11824      2
11826           11825      2
11827           11826      2
11828           11827      2
3827             3826      2

[18662 rows x 2 columns]

In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID"] == -1:
        print(row["Код"], row["Normalized"])

НИ-000043138 cухой паёк офицерский армейский будни рпс
НИ-IS0000748 dallas lock c сзи нсд скн
НИ-IS0043559 kольцо крепление груз нагрузка оцинкованное железо оснастить крепёжный винт серебро штука
НИ-IS0050230 автобензин премиум евро
НИ-IS0036921 автозапчасть
НИ-IS0022695 автоэмаль акрил 08 килограмм
НИ-IS0040897 адаптер hn200325ep0 ноутбук honor huawei hw200325cp0 hw200325cpo hq200325epo hq200325ep0 hn200325epo
НИ-IS0034792 адаптер шуруповертов ресанта 18в да лк
НИ-IS0036530 адаптер мультипортовый usb ugreen multifunction adapter
НИ-IS0036772 адаптер проходной эра rj45rj45
НИ-IS0045892 адгезив силбонд 49sfc 08 килограмм
НИ-IS0049065 азот 40 литр 62
НИ-IS0025275 аккум ушм 18в
НИ-IS0026360 аккумулятор актех униклемма
НИ-IS0023396 аккумулятор ст тракт низкий
НИ-IS0041815 аккумулятор gp r6 аа ni mh 2700mah box 10шт
НИ-IS0045204 аккумулятор hb4692z9ecw22a matebook 64v 56wh 7330mah
НИ-IS0041083 аккумулятор toolyard 21v ач li ion akb007
НИ-IS0038845 аккумулятор перезаряжать nutritionmag пита

In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID_DBSCAN"] == -1:
        print(row["Код"], row["Normalized"])

НИ-IS0032430 cветильник led панель 50w 6500k ip40 1200 миллиметр дпо призма neox
НИ-IS0040225 cветильник потолочный osairous 30вт led 6500 светодиодный потолочный
НИ-IS0047648 cпрей ванный комната sanfor санфор 500 миллилитр
НИ-IS0047649 cпрей ультрабелый sanfor санфор 500 миллилитр
НИ-IS0047659 cредство чистить биолан 400 сочный яблоко нэфис
НИ-IS0023737 cтиральный порошок персил 21 килограмм
НИ-IS0047372 cтроп цепной сц одноветвевой стандартный2 метр
НИ-000043138 cухой паёк офицерский армейский будни рпс
НИ-IS0000748 dallas lock c сзи нсд скн
НИ-IS0043559 kольцо крепление груз нагрузка оцинкованное железо оснастить крепёжный винт серебро штука
НИ-IS0036921 автозапчасть
НИ-IS0052984 автолампа а24 5 24v маяк россия
НИ-IS0046878 автомат дифференциальный авдт c 4p 32a характеристика
НИ-IS0046879 автомат дифференциальный авдт c 4p 20a характеристика
НИ-IS0031012 автоматический выключатель постоянный ток nb1 63dc 2p c2a dc500b 6ka chint
НИ-IS0034255 автотрансформатор латр tdgc25 аосн andel

In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID"] == 9:
        print(row["Normalized"])

автолампа а24 5 24v маяк россия
автолампа


In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID"] == 10:
        print(row["Normalized"])

автолампочка н7 70w фарная галогеновая уп штука
лампа фарная галогеновая акг


In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID_DBSCAN"] == 3:
        print(row["Normalized"])

автошампунь бесконтактный мойка активный пена kraft gold 20 килограмм
автошампунь бесконтактный мойка grass active foam red пена 23 килограмм
автошампунь бесконтактный мойка активный пена active foam magic килограмм
средство мыть grass active foam pink 235 килограмм
средство мыть grass active foam red литр
средство мыть grass active foam power килограмм


In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID_DBSCAN"] == 2:
        print(row["Normalized"])

автошампунь grass active foam truck cуперпена безконтактной мойка грузовик 24 кг
автошампунь grass active foam effect литр
автошампунь grass active foam light 5000 миллилитр


In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID_DBSCAN"] == 4:
        print(row["Normalized"])

автоэмаль reoflex акр 08 литр
автоэмаль reoflex акр 08 литр штука
автоэмаль reoflex акр toy 3p0 super red литр штука
автоэмаль reoflex акр 08 литр штука
грунт reoflex 1hs акр 08 литр 16л штука штука


In [ ]:
for i, row in df.iterrows():
    if row["Cluster_ID_DBSCAN"] == 8:
        print(row["Normalized"])

аккумулятор re03xl ноутбук hp probook g6 55v 3500mah premium
аккумулятор rr03xl ноутбук hp probook g4 4v 3930mah premium
ноутбук hp probook g6 fhd core i7 8565u win10pro 5pq22ea acb
ноутбук hp probook g8 43a28ea
ноутбук hp probook g6 5pq02ea core i5 8265u 6ghz fhd ag8gb ddr4 256 gb ssd nvidia gf mx130 2gb ddr545wh ll fpr win10pro
ноутбук hp probook g6 i5 win10 pro зав 5cd9462103
ноутбук hp probook g6 i5 win10 pro зав 5cd9514j63
ноутбук hp probook g8 intel core i7 1165g7 16 гб ssd гб ос 2x7w9ea16


In [ ]:
# print(*filter(lambda x: x[1] > 2, count.items()), sep="\n")
count_int = {}
for _, coun in count.items():
    count_int[coun] = count_int.get(coun, 0) + 1
count_int

{50942: 1,
 2: 10821,
 3: 3851,
 8: 342,
 6: 626,
 4: 1813,
 5: 934,
 29: 9,
 9: 244,
 11: 131,
 54: 4,
 17: 47,
 10: 186,
 12: 105,
 28: 13,
 23: 17,
 32: 10,
 7: 404,
 35: 6,
 47: 6,
 16: 64,
 13: 91,
 21: 26,
 22: 14,
 105: 1,
 38: 1,
 14: 80,
 18: 44,
 19: 44,
 15: 61,
 59: 2,
 26: 17,
 41: 2,
 24: 14,
 31: 8,
 239: 1,
 88: 1,
 20: 25,
 42: 5,
 343: 1,
 25: 11,
 37: 7,
 57: 2,
 33: 6,
 62: 3,
 43: 4,
 45: 5,
 30: 5,
 98: 1,
 40: 7,
 64: 3,
 46: 11,
 48: 2,
 34: 9,
 69: 1,
 102: 1,
 146: 1,
 36: 6,
 27: 12,
 53: 1,
 44: 3,
 60: 1,
 78: 2,
 50: 4,
 39: 4,
 51: 1,
 67: 1,
 99: 1,
 108: 1,
 77: 2,
 68: 1,
 85: 1,
 79: 1,
 97: 1,
 80: 1,
 56: 1,
 49: 1,
 61: 1,
 74: 1,
 52: 1}